In [2]:
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager

def get_driver():
    options = Options()
    # Set your Brave browser executable path here
    options.binary_location = r"C:\Program Files\BraveSoftware\Brave-Browser\Application\brave.exe"  # Change for your OS
    
    options.add_argument('--headless')  # Remove if you want to see the browser
    options.add_argument('--no-sandbox')
    options.add_argument('--disable-dev-shm-usage')
    options.add_argument('--disable-gpu')
    options.add_argument('window-size=1920,1080')
    options.add_argument('user-agent=Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/115.0.0.0 Safari/537.36')
    
    # This will automatically download and use the correct ChromeDriver version matching your Brave Chromium
    service = Service(ChromeDriverManager().install())
    
    driver = webdriver.Chrome(service=service, options=options)
    return driver

In [5]:
import time
import pandas as pd
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager
from bs4 import BeautifulSoup

BASE_URL = "https://www.basketball-reference.com"
PLAYER_IDS_CSV = "player_ids.csv"

def get_driver():
    options = Options()
    options.binary_location = r"C:\Program Files\BraveSoftware\Brave-Browser\Application\brave.exe"
    options.add_argument('--headless')
    options.add_argument('--no-sandbox')
    options.add_argument('--disable-dev-shm-usage')
    options.add_argument('--disable-gpu')
    options.add_argument('window-size=1920,1080')
    options.add_argument('user-agent=Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/115.0.0.0 Safari/537.36')
    service = Service(ChromeDriverManager().install())
    driver = webdriver.Chrome(service=service, options=options)
    return driver

def scrape_player_ids(driver, letter):
    url = f"{BASE_URL}/players/{letter}/"
    driver.get(url)
    time.sleep(3)
    soup = BeautifulSoup(driver.page_source, 'html.parser')
    table = soup.find('table', id='players')
    if not table:
        print(f"No player table found for letter {letter}")
        return []
    player_ids = []
    for row in table.tbody.find_all('tr'):
        if row.get('class') and 'thead' in row.get('class'):
            continue
        player_link = row.find('a')
        if player_link and 'href' in player_link.attrs:
            href = player_link['href']
            player_id = href.split('/')[-1].replace('.html', '')
            player_name = player_link.text.strip()
            player_ids.append((player_id, player_name))
    return player_ids

def save_player_ids(player_ids, path):
    df = pd.DataFrame(player_ids, columns=['PlayerID', 'PlayerName'])
    df.to_csv(path, index=False)
    print(f"Saved {len(player_ids)} player IDs to {path}")

def main():
    driver = get_driver()
    all_player_ids = []
    for letter in 'abcdefghijklmnopqrstuvwxyz':
        print(f"Scraping player IDs for letter {letter.upper()}...")
        player_ids_letter = scrape_player_ids(driver, letter)
        print(f"Found {len(player_ids_letter)} players for letter {letter.upper()}.")
        all_player_ids.extend(player_ids_letter)
    print(f"Total players found: {len(all_player_ids)}")
    save_player_ids(all_player_ids, PLAYER_IDS_CSV)
    driver.quit()

if __name__ == "__main__":
    main()

Scraping player IDs for letter A...
Found 178 players for letter A.
Scraping player IDs for letter B...
Found 508 players for letter B.
Scraping player IDs for letter C...
Found 335 players for letter C.
Scraping player IDs for letter D...
Found 264 players for letter D.
Scraping player IDs for letter E...
Found 116 players for letter E.
Scraping player IDs for letter F...
Found 161 players for letter F.
Scraping player IDs for letter G...
Found 265 players for letter G.
Scraping player IDs for letter H...
Found 376 players for letter H.
Scraping player IDs for letter I...
Found 29 players for letter I.
Scraping player IDs for letter J...
Found 263 players for letter J.
Scraping player IDs for letter K...
Found 183 players for letter K.
Scraping player IDs for letter L...
Found 209 players for letter L.
Scraping player IDs for letter M...
Found 502 players for letter M.
Scraping player IDs for letter N...
Found 112 players for letter N.
Scraping player IDs for letter O...
Found 97 play

In [10]:
import os
import time
import pandas as pd
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager
from bs4 import BeautifulSoup, Comment

BASE_URL = "https://www.basketball-reference.com"
OUTPUT_CSV = "all_players_stats_2000_2025.csv"
PLAYER_IDS_CSV = "player_ids.csv"

def get_driver():
    options = Options()
    options.binary_location = r"C:\Program Files\BraveSoftware\Brave-Browser\Application\brave.exe"
    options.add_argument('--headless')
    options.add_argument('--no-sandbox')
    options.add_argument('--disable-dev-shm-usage')
    options.add_argument('--disable-gpu')
    options.add_argument('window-size=1920,1080')
    options.add_argument('user-agent=Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/115.0.0.0 Safari/537.36')
    service = Service(ChromeDriverManager().install())
    driver = webdriver.Chrome(service=service, options=options)
    return driver

def load_player_ids(path):
    if os.path.isfile(path):
        df = pd.read_csv(path)
        player_ids = list(zip(df['PlayerID'], df['PlayerName']))
        print(f"Loaded {len(player_ids)} player IDs from {path}")
        return player_ids
    else:
        raise FileNotFoundError(f"{path} not found. Run player ID scraping first.")

def extract_table_from_html(soup, table_id):
    table = soup.find('table', id=table_id)
    if table:
        return pd.read_html(str(table))[0]
    comments = soup.find_all(string=lambda text: isinstance(text, Comment))
    for comment in comments:
        comment_soup = BeautifulSoup(comment, 'html.parser')
        table = comment_soup.find('table', id=table_id)
        if table:
            return pd.read_html(str(table))[0]
    print(f"Table with id '{table_id}' not found in page.")
    return None

def filter_stats_by_season(df, start_year=2000, end_year=2025):
    if df is None or df.empty:
        return None
    if 'Season' not in df.columns:
        return None
    def season_year(season_str):
        try:
            return int(season_str[:4])
        except:
            return None
    df['SeasonYear'] = df['Season'].apply(season_year)
    filtered_df = df[(df['SeasonYear'] >= start_year) & (df['SeasonYear'] <= end_year)]
    if filtered_df.empty:
        return None
    filtered_df = filtered_df.drop(columns=['SeasonYear'])
    return filtered_df

from bs4 import BeautifulSoup, Comment

def inspect_tables_in_page(html):
    soup = BeautifulSoup(html, 'html.parser')
    
    print("Tables found directly in HTML:")
    tables = soup.find_all('table')
    for table in tables:
        if 'id' in table.attrs:
            print(f" - {table['id']}")
    
    print("\nTables found inside HTML comments:")
    comments = soup.find_all(string=lambda text: isinstance(text, Comment))
    for comment in comments:
        comment_soup = BeautifulSoup(comment, 'html.parser')
        tables = comment_soup.find_all('table')
        for table in tables:
            if 'id' in table.attrs:
                print(f" - {table['id']}")

# Usage example inside your scrape_player_stats function:

def scrape_player_stats(driver, player_id):
    first_letter = player_id[0]
    url = f"{BASE_URL}/players/{first_letter}/{player_id}.html"
    driver.get(url)
    time.sleep(3)
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Extract per-game stats directly
    per_game_df = extract_table_from_html(soup, 'per_game_stats')
    advanced_df = extract_table_from_html(soup, 'advanced')

    per_game_df = filter_stats_by_season(per_game_df)
    advanced_df = filter_stats_by_season(advanced_df)

    return per_game_df, advanced_df
    
def append_player_stats_to_csv(player_name, player_id, per_game_df, advanced_df, output_csv=OUTPUT_CSV):
    if per_game_df is None and advanced_df is None:
        return
    if per_game_df is not None:
        per_game_df = per_game_df.copy()
        per_game_df['PlayerName'] = player_name
        per_game_df['PlayerID'] = player_id
    if advanced_df is not None:
        advanced_df = advanced_df.copy()
        advanced_df['PlayerName'] = player_name
        advanced_df['PlayerID'] = player_id
    if per_game_df is not None and advanced_df is not None:
        merged_df = pd.merge(
            per_game_df,
            advanced_df,
            on=['Season', 'Team', 'Lg'],
            suffixes=('_per_game', '_adv'),
            how='outer'
        )
        merged_df['PlayerName'] = player_name
        merged_df['PlayerID'] = player_id
    elif per_game_df is not None:
        merged_df = per_game_df
    else:
        merged_df = advanced_df
    if not os.path.isfile(output_csv):
        merged_df.to_csv(output_csv, index=False)
    else:
        merged_df.to_csv(output_csv, mode='a', header=False, index=False)
    print(f"Appended stats for {player_name} ({player_id})")

def main():
    driver = get_driver()
    player_ids = load_player_ids(PLAYER_IDS_CSV)
    scraped_ids = set()
    if os.path.isfile(OUTPUT_CSV):
        df_existing = pd.read_csv(OUTPUT_CSV, usecols=['PlayerID'])
        scraped_ids = set(df_existing['PlayerID'].unique())
        print(f"Resuming, already scraped {len(scraped_ids)} players.")
    for idx, (player_id, player_name) in enumerate(player_ids):
        if player_id in scraped_ids:
            print(f"Skipping already scraped player {player_name} ({player_id}) [{idx+1}/{len(player_ids)}]")
            continue
        print(f"Scraping stats for {player_name} ({player_id}) [{idx+1}/{len(player_ids)}]")
        per_game_df, advanced_df = scrape_player_stats(driver, player_id)
        if per_game_df is None and advanced_df is None:
            print(f"No stats in 2000-2025 for {player_name} ({player_id}), skipping.")
            continue
        append_player_stats_to_csv(player_name, player_id, per_game_df, advanced_df)
        time.sleep(3)  # polite delay
    driver.quit()

if __name__ == "__main__":
    main()

Loaded 5313 player IDs from player_ids.csv
Scraping stats for Alaa Abdelnaby (abdelal01) [1/5313]


C:\Users\furla\AppData\Local\Temp\ipykernel_41568\914129260.py:39: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  return pd.read_html(str(table))[0]
C:\Users\furla\AppData\Local\Temp\ipykernel_41568\914129260.py:39: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  return pd.read_html(str(table))[0]


No stats in 2000-2025 for Alaa Abdelnaby (abdelal01), skipping.
Scraping stats for Zaid Abdul-Aziz (abdulza01) [2/5313]


C:\Users\furla\AppData\Local\Temp\ipykernel_41568\914129260.py:39: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  return pd.read_html(str(table))[0]
C:\Users\furla\AppData\Local\Temp\ipykernel_41568\914129260.py:39: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  return pd.read_html(str(table))[0]


No stats in 2000-2025 for Zaid Abdul-Aziz (abdulza01), skipping.
Scraping stats for Kareem Abdul-Jabbar (abdulka01) [3/5313]


...

No stats in 2000-2025 for Bill Zopf (zopfbi01), skipping.
Scraping stats for Ivica Zubac (zubaciv01) [5312/5313]


C:\Users\furla\AppData\Local\Temp\ipykernel_41568\914129260.py:39: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  return pd.read_html(str(table))[0]
C:\Users\furla\AppData\Local\Temp\ipykernel_41568\914129260.py:39: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  return pd.read_html(str(table))[0]


Appended stats for Ivica Zubac (zubaciv01)
Scraping stats for Matt Zunic (zunicma01) [5313/5313]


C:\Users\furla\AppData\Local\Temp\ipykernel_41568\914129260.py:39: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  return pd.read_html(str(table))[0]
C:\Users\furla\AppData\Local\Temp\ipykernel_41568\914129260.py:39: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  return pd.read_html(str(table))[0]


No stats in 2000-2025 for Matt Zunic (zunicma01), skipping.
